## Linear regression of house prices data

---



In [2]:
import numpy as np
import pandas as pd
import plotly.graph_objects as go
import plotly.express as px

EPSILON = 10**(-8)
PATH = r'./kc_house_data.csv' 

In [3]:
def add_intercept_col(X):
  return np.c_[np.ones(X.shape[0]), X]

def get_pseudoinvese_mat(X): # we asuume: m >= d+1. X dim: mX(d+1)
  u, s, vh = np.linalg.svd(X, full_matrices=True, compute_uv=True) # u: mXm, s: mX(d+1), vh: (d+1)X(d+1)
  s_cross = np.zeros((X.shape[1], X.shape[0])) # (d+1) x (m)
  for i in range(len(s)):
    if (s[i] != 0):
      val = 1/s[i]
      if val > EPSILON:
        s_cross[i,i] = val
  return s, np.matmul(np.matmul(vh.T, s_cross), u.T)
 
def fit_linear_regression(X, y):
  """
  fits linear_regression using svd decomposition. 
  returns the calculated weights, and the singular values derevied
  from the pseudoinvese matrix
  """
  if (X.shape[0] < X.shape[1] + 1) or (y.shape[0] < X.shape[0]): return
  X = add_intercept_col(X)
  singular_vals, pseudoinvese_mat = get_pseudoinvese_mat(X)
  weights = np.matmul(pseudoinvese_mat, y)
  return weights, singular_vals

def predict(X, weights):
  if X.shape[1] != len(weights):
    X = add_intercept_col(X)
    return np.matmul(X, weights)

def mse(response, prediction):
  diff = response - prediction
  pw_diff = np.power(diff, 2)
  return (1/len(diff))*pw_diff.sum()


def plot_singular_values(val_arr, log=False):
  x = np.arange(len(val_arr)) + 1
  fig = go.Figure([go.Scatter(x=x, y=val_arr, name="value", showlegend=True,
                                 marker=dict(color="black", opacity=.6), line=dict(color="black", dash="dash", width=0.5))], 
          layout=go.Layout(title=r"Singular values",
                           xaxis={"title": "Singular value's index", "tickmode": "linear"},
                           yaxis={"title": "Singular value' value"},
                           height=400))
  if (log==True):
      fig.update_yaxes(type="log", range=[0,7])
  fig.show()

def plot_mse_values(val_arr, log=False):
  x = np.arange(len(val_arr)) + 1
  fig = go.Figure([go.Scatter(x=x, y=val_arr, name="value", showlegend=True,
                                marker=dict(color="black", opacity=.6), line=dict(color="black", dash="dash", width=0.5))], 
          layout=go.Layout(title="MSE values",
                          xaxis={"title": "Percentage of train set", "tickmode": "linear"},
                          yaxis={"title": "MSE value"},
                          height=400))
  if (log==True):
      fig.update_yaxes(type="log")
  fig.show()  


def load_data(path, one_mat=False):

  design_mat = pd.read_csv(path)
  # filtering
  design_mat = design_mat.loc[design_mat['price'] > 0]
  design_mat = design_mat.loc[design_mat['bedrooms'] > 0]
  # Note: in this data these two are sufficient to clear 
  # all illegals vals from other cols (e.g when sqft_living = 0, bedrooms = 0 too)


  # Adressing categorical variables and other preproccesing
  design_mat['year_2015'] = np.where(design_mat['date'].str.contains("2015"),1,0)
  
  design_mat['yrs_s_renov'] = (2014 + design_mat['year_2015']) - \
                 design_mat[["yr_built", "yr_renovated"]  ].max(axis=1)
  design_mat['decade'] = (design_mat['yr_built']//10)*10
  design_mat = pd.concat([design_mat, pd.get_dummies(design_mat['decade'])],axis=1).drop(['decade'], axis=1).drop([2010.0], axis=1)
  design_mat = pd.concat([design_mat, pd.get_dummies(design_mat['zipcode'])], \
                                                             axis=1).drop([98002.0], axis=1)


  # dropping unneccesary and original cols
  design_mat = design_mat.drop(['id'], axis=1)
  design_mat = design_mat.drop(['date'], axis=1)
  design_mat = design_mat.drop(['lat'], axis=1)
  design_mat = design_mat.drop(['long'], axis=1)
  design_mat = design_mat.drop(['zipcode'], axis=1)
  design_mat = design_mat.drop(['yr_built'], axis=1)
  design_mat = design_mat.drop(['yr_renovated'], axis=1)

  if (one_mat == True):
    return design_mat

  return design_mat.drop(['price'], axis=1), design_mat['price']


# Plotting a scree-plot. 
The matrix is close to singular: the least singular values are close to zero.
In other words, there is strong colinearity in our model.
Even if we would cast away the corresponding feature, the explanatory power of most of the dummy variables we generated, and of some other variables, is very weak, at least as **linear** factors of buildings’ prices.

In [3]:
X, y = load_data(PATH)
weights, singular_vals = fit_linear_regression(X.to_numpy(), y.to_numpy())
plot_singular_values(singular_vals, True)

# MSE vs. trainnig data size
We can see that a bigger training set improves our model predictions until a certain point, and the improvement is negatable. We can deduce:
Our model gives very imprecise predictions. The real connection between the factors and the prices, if exists, is not linear.


In [4]:
MAX_P = 1
des_mat = load_data(PATH, True)
data_len = len(des_mat)
msk = np.random.rand(data_len) < 0.75
train = des_mat[msk]
test = des_mat[~msk]
p_set = np.linspace(0.01, MAX_P, int(100*MAX_P))
mse_val = []

for p in p_set: 
  X_p, y_p = train.drop(['price'], axis=1).head(int(p*len(train))), train['price'].head(int(p*len(train)))
  weights, singular_vals = fit_linear_regression(X_p.to_numpy(), y_p.to_numpy())
  y_hat = predict(test.drop(['price'], axis=1).to_numpy(), weights)
  mse_val.append(mse(test['price'].to_numpy(), y_hat))

plot_mse_values(mse_val, True)

# Pearson Correlation
A clear beneficial feature is sqft_above: the Pearson correlation here is quite strong. The
scatter plot also confirms: the bigger sqft_above is, the higher the price is, in most of the cases.

It turned out that the feature I generated from the data: Years since the last renovation, is not that
helpful in our model. As expected, the correlation is slightly negative, but gives a little
information, as the plot shows.

In [12]:
def pearson_corr(vec_1, vec_2):
  return (np.cov(vec_1,vec_2)[0][1])/(np.std(vec_1)*np.std(vec_2))

def feature_evaluation(design_mat, response_vec):
  for col in design_mat:
    if len(design_mat[col].unique()) < 3: # drop dummies
      design_mat = design_mat.drop([col], axis=1)   
# 17 Pearson Correlation
  for i, feature in enumerate(design_mat):
      # if i > 4: # plotly sometimes crashes when many plots are generated. Use this to see the first plots.
      #   break;  # Use these lines to see the first plots.
      p_corr = pearson_corr(design_mat[feature].to_numpy(), response_vec.to_numpy())
      label = "Feature: " + feature +". Pearson Correlation: " + str(round(p_corr, 4))
      df = pd.concat([design_mat[feature], response_vec], axis=1)
      figure = px.scatter(df, x=feature, y="price", title=label)
      figure.show()

data, response = load_data(PATH)
feature_evaluation(data, response)